# Classification multi-classe

On cherche à prédire la note d'un vin avec un classifieur multi-classe.

In [1]:
%matplotlib inline

In [3]:
from teachpyx.datasets import load_wines_dataset

df = load_wines_dataset()
X = df.drop(["quality", "color"], axis=1)
y = df["quality"]

In [4]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(X, y)

In [6]:
from sklearn.linear_model import LogisticRegression

clr = LogisticRegression(solver="liblinear")
clr.fit(X_train, y_train)

LogisticRegression(solver='liblinear')

In [7]:
import numpy

numpy.mean(clr.predict(X_test).ravel() == y_test.ravel()) * 100

55.07692307692308

On regarde la matrice de confusion.

In [8]:
from sklearn.metrics import confusion_matrix
import pandas

pandas.DataFrame(confusion_matrix(y_test, clr.predict(X_test)))

0  1    2    3   4  5  6
0  0  0    4    7   0  0  0
1  0  0   47   22   0  0  0
2  0  0  332  184   0  0  0
3  0  0  169  541  10  0  0
4  0  0   19  217  22  0  0
5  0  0    3   42   5  0  0
6  0  0    0    1   0  0  0

On l'affiche différemment avec le nom des classes.

In [9]:
conf = confusion_matrix(y_test, clr.predict(X_test))
dfconf = pandas.DataFrame(conf)
labels = list(clr.classes_)
if len(labels) < dfconf.shape[1]:
    labels += [
        9
    ]  # La classe 9 est très représentée, elle est parfois absente en train.
elif len(labels) > dfconf.shape[1]:
    labels = labels[: dfconf.shape[1]]  # ou l'inverse
dfconf.columns = labels
dfconf.index = labels
dfconf

3  4    5    6   7  8  9
3  0  0    4    7   0  0  0
4  0  0   47   22   0  0  0
5  0  0  332  184   0  0  0
6  0  0  169  541  10  0  0
7  0  0   19  217  22  0  0
8  0  0    3   42   5  0  0
9  0  0    0    1   0  0  0

Pas extraordinaire. On applique la stratégie [OneVsRestClassifier](https://scikit-learn.org/stable/modules/generated/sklearn.multiclass.OneVsRestClassifier.html).

In [10]:
from sklearn.multiclass import OneVsRestClassifier

clr = OneVsRestClassifier(LogisticRegression(solver="liblinear"))
clr.fit(X_train, y_train)

OneVsRestClassifier(estimator=LogisticRegression(solver='liblinear'))

In [11]:
numpy.mean(clr.predict(X_test).ravel() == y_test.ravel()) * 100

54.95384615384615

Le modèle logistique régression multi-classe est équivalent à la stratégie *OneVsRest*. Voyons l'autre.

In [12]:
from sklearn.multiclass import OneVsOneClassifier

clr = OneVsOneClassifier(LogisticRegression(solver="liblinear"))
clr.fit(X_train, y_train)

OneVsOneClassifier(estimator=LogisticRegression(solver='liblinear'))

In [13]:
numpy.mean(clr.predict(X_test).ravel() == y_test.ravel()) * 100

55.138461538461534

In [14]:
conf = confusion_matrix(y_test, clr.predict(X_test))
dfconf = pandas.DataFrame(conf)
labels = list(clr.classes_)
if len(labels) < dfconf.shape[1]:
    labels += [
        9
    ]  # La classe 9 est très représentée, elle est parfois absente en train.
elif len(labels) > dfconf.shape[1]:
    labels = labels[: dfconf.shape[1]]  # ou l'inverse
dfconf.columns = labels
dfconf.index = labels
dfconf

3  4    5    6   7  8  9
3  0  0    5    6   0  0  0
4  0  0   46   23   0  0  0
5  0  0  332  183   1  0  0
6  0  0  169  524  27  0  0
7  0  0   18  200  40  0  0
8  0  0    6   32  12  0  0
9  0  0    0    1   0  0  0

A peu près pareil mais sans doute pas de manière significative. Voyons avec un arbre de décision.

In [15]:
from sklearn.tree import DecisionTreeClassifier

clr = DecisionTreeClassifier()
clr.fit(X_train, y_train)

DecisionTreeClassifier()

In [16]:
numpy.mean(clr.predict(X_test).ravel() == y_test.ravel()) * 100

59.323076923076925

Et avec [OneVsRestClassifier](https://scikit-learn.org/stable/modules/generated/sklearn.multiclass.OneVsRestClassifier.html) :

In [17]:
clr = OneVsRestClassifier(DecisionTreeClassifier())
clr.fit(X_train, y_train)

OneVsRestClassifier(estimator=DecisionTreeClassifier())

In [18]:
numpy.mean(clr.predict(X_test).ravel() == y_test.ravel()) * 100

53.35384615384615

Et avec [OneVsOneClassifier](https://scikit-learn.org/stable/modules/generated/sklearn.multiclass.OneVsOneClassifier.html)

In [19]:
clr = OneVsOneClassifier(DecisionTreeClassifier())
clr.fit(X_train, y_train)

OneVsOneClassifier(estimator=DecisionTreeClassifier())

In [20]:
numpy.mean(clr.predict(X_test).ravel() == y_test.ravel()) * 100

62.58461538461538

Mieux.

In [21]:
from sklearn.ensemble import RandomForestClassifier

clr = RandomForestClassifier()
clr.fit(X_train, y_train)

RandomForestClassifier()

In [23]:
numpy.mean(clr.predict(X_test).ravel() == y_test.ravel()) * 100

69.2923076923077

In [24]:
clr = OneVsRestClassifier(RandomForestClassifier())
clr.fit(X_train, y_train)

OneVsRestClassifier(estimator=RandomForestClassifier())

In [25]:
numpy.mean(clr.predict(X_test).ravel() == y_test.ravel()) * 100

69.41538461538461

Proche, il faut affiner avec une validation croisée.

In [26]:
from sklearn.neural_network import MLPClassifier

clr = MLPClassifier(hidden_layer_sizes=30, max_iter=600)
clr.fit(X_train, y_train)

MLPClassifier(hidden_layer_sizes=30, max_iter=600)

In [27]:
numpy.mean(clr.predict(X_test).ravel() == y_test.ravel()) * 100

52.800000000000004

In [28]:
clr = OneVsRestClassifier(MLPClassifier(hidden_layer_sizes=30, max_iter=600))
clr.fit(X_train, y_train)

OneVsRestClassifier(estimator=MLPClassifier(hidden_layer_sizes=30,
                                            max_iter=600))

In [29]:
numpy.mean(clr.predict(X_test).ravel() == y_test.ravel()) * 100

52.800000000000004

Pas foudroyant.